### This .ipynb file performs Exploratory Data Analysis on a product_a.csv data set which contains the sales information of two types of products (A and C) for different locations in United States over a span of 4 years

##### Import required libraries

In [96]:
import pandas as pd
import numpy as np

import plotly.graph_objs as go
import plotly.express.colors as plotly_colors
import plotly_express as px
from plotly.offline import plot, iplot
from plotly.subplots import make_subplots
import folium

from arcgis.gis import GIS
from arcgis.geocoding import batch_geocode
import requests

## Product A

product_a.csv file contains ~ 18K samples and 13 columns represententing sales data over span of four year period ranging from 2016 - 2019 in different states of USA

In [138]:
# read csv file with first column as index column, first row as header and parse date_w to datetime
df_product_a = pd.read_csv("product_a.csv", sep = ",", header = 0 , index_col = 0, parse_dates = [1], dayfirst = True)

# update year column with year specified in the date_w column as there were few incorrect values in year column
df_product_a['year'] = pd.DatetimeIndex(df_product_a['date_w']).year

# change the data type of year column from numeric to categorical (ordered)
#df_product_a['year'] = df_product_a['year'].astype(pd.api.types.CategoricalDtype(categories=["2016", "2017", "2018", "2019"], ordered=True))

df_product_a.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 18249 entries, 0 to 11
Data columns (total 13 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   date_w     18249 non-null  datetime64[ns]
 1   price      18249 non-null  float64       
 2   total_vol  18249 non-null  float64       
 3   plu1       18249 non-null  float64       
 4   plu2       18249 non-null  float64       
 5   plu3       18249 non-null  float64       
 6   bags_t     18249 non-null  float64       
 7   bags_s     18249 non-null  float64       
 8   bags_l     18249 non-null  float64       
 9   bags_lx    18249 non-null  float64       
 10  type       18249 non-null  object        
 11  year       18249 non-null  int64         
 12  location   18249 non-null  object        
dtypes: datetime64[ns](1), float64(9), int64(1), object(2)
memory usage: 1.9+ MB


## Data

In [98]:
df_product_a

date_w     price      total_vol         plu1           plu2  \
0  2016-12-24 1.3300000  64236.6200000 1036.7400000  54454.8500000   
1  2016-12-17 1.3500000  54876.9800000  674.2800000  44638.8100000   
2  2016-12-10 0.9300000 118220.2200000  794.7000000 109149.6700000   
3  2016-12-03 1.0800000  78992.1500000 1132.0000000  71976.4100000   
4  2016-11-26 1.2800000  51039.6000000  941.4800000  43838.3900000   
..        ...       ...            ...          ...            ...   
7  2019-02-02 1.6300000  17074.8300000 2046.9600000   1529.2000000   
8  2019-01-26 1.7100000  13888.0400000 1191.7000000   3431.5000000   
9  2019-01-19 1.8700000  13766.7600000 1191.9200000   2452.7900000   
10 2019-01-12 1.9300000  16205.2200000 1527.6300000   2981.0400000   
11 2019-01-05 1.6200000  17489.5800000 2894.7700000   2356.1300000   

          plu3        bags_t        bags_s      bags_l   bags_lx type  year  \
0   48.1600000  8696.8700000  8603.6200000  93.2500000 0.0000000    A  2016   
1   58.3300000  9505.5600000  9408.0700000  97.4900000 0.0000000    A  2016   
2  130.5000000  8145.3500000  8042.2100000 103.1400000 0.0000000    A  2016   
3   72.5800000  5811.1600000  5677.4000000 133.7600000 0.0000000    A  2016   
4   75.7800000  6183.9500000  5986.2600000 197.6900000 0.0000000    A  2016   
..         ...           ...           ...         ...       ...  ...   ...   
7    0.0000000 13498.6700000 13066.8200000 431.8500000 0.0000000    C  2019   
8    0.0000000  9264.8400000  8940.0400000 324.8000000 0.0000000    C  2019   
9  727.9400000  9394.1100000  9351.8000000  42.3100000 0.0000000    C  2019   
10 727.0100000 10969.5400000 10919.5400000  50.0000000 0.0000000    C  2019   
11 224.5300000 12014.1500000 11988.1400000  26.0100000 0.0000000    C  2019   

            location  
0             Albany  
1             Albany  
2             Albany  
3             Albany  
4             Albany  
..               ...  
7   WestTexNewMexico  
8   WestTexNewMexico  
9   WestTexNewMexico  
10  WestTexNewMexico  
11  WestTexNewMexico  

[18249 rows x 13 columns]

## Missing values
Data contains no missing values

In [99]:
df_product_a.isna().sum()

date_w       0
price        0
total_vol    0
plu1         0
plu2         0
plu3         0
bags_t       0
bags_s       0
bags_l       0
bags_lx      0
type         0
year         0
location     0
dtype: int64

## Descriptive statistics

The below data-frame shows the descriptive statistics for various numerical columns of product_a.csv

- The mean values for all the columns are much higher than the median values which indicates that the data for all of them is right skewed i.e. non symmetrical data. It can be explained with the the positive values of 'skewness'

- From the summary we can clearly see that there is high variability in data for almost all the columns as the minimum values are in few hundreds in contrast to maximum values which are in millions, thereby justifying the high values of 'variance'

- Also, according to the statistics shown below we can say that there are many outliers for all the attributes as the 80th and 90th quantiles lie much far from the IQR range

- Large positive values for 'kurtosis' indicates that the data is too peaked and it is not normally distributed

In [100]:
pd.set_option('display.float_format', lambda x: '%.7f' % x)

# separate numeric columns form df_product_a to calculate descriptive statistics
df_stats = df_product_a.select_dtypes(include = 'number').drop(columns = ['year'], axis=1).copy()

# calculate quantiles for 0.1, 0.2 .. 0.9
summary_df = df_stats.describe(percentiles=np.arange(0.1,1,0.10).tolist())

# calculate the IQR (where the middle 50% of data lies)
summary_df.loc['IQR'] = df_stats.quantile(0.75) - df_stats.quantile(0.25)

summary_df.loc['median'] = df_stats.median()
summary_df.loc['variance'] = df_stats.var()
summary_df.loc['skewness'] = df_stats.skew()
summary_df.loc['kutosis'] = df_stats.kurt()

summary_df.transpose()

count           mean             std        min  \
price     18249.0000000      1.4059784       0.4026766  0.4400000   
total_vol 18249.0000000 850644.0130089 3453545.3553995 84.5600000   
plu1      18249.0000000 293008.4245307 1264989.0817628  0.0000000   
plu2      18249.0000000 295154.5683561 1204120.4011351  0.0000000   
plu3      18249.0000000  22839.7359927  107464.0684354  0.0000000   
bags_t    18249.0000000 239639.2020598  986242.3992164  0.0000000   
bags_s    18249.0000000 182194.6866957  746178.5149618  0.0000000   
bags_l    18249.0000000  54338.0881446  243965.9645474  0.0000000   
bags_lx   18249.0000000   3106.4265072   17692.8946519  0.0000000   

                   10%          20%           30%           40%  \
price        0.9300000    1.0500000     1.1500000     1.2600000   
total_vol 3896.7680000 8168.8660000 15181.3040000 42137.0880000   
plu1        94.2760000  483.3620000  1368.1180000  3261.5800000   
plu2       367.4840000 1918.5320000  4265.5080000 10961.9940000   
plu3         0.0000000    0.0000000     0.0000000    42.7040000   
bags_t    1299.2080000 3347.6740000  7316.6340000 16643.2600000   
bags_s     583.1100000 1686.0860000  4761.3280000 11502.0760000   
bags_l       0.0000000   30.9180000   329.9440000  1105.1100000   
bags_lx      0.0000000    0.0000000     0.0000000     0.0000000   

                     50%            60%            70%            80%  \
price          1.3700000      1.4800000      1.6000000      1.7400000   
total_vol 107376.7600000 192430.1240000 319613.1420000 604868.9680000   
plu1        8645.3000000  31698.0780000  77991.4100000 152679.0680000   
plu2       29061.0200000  53202.0520000  98296.1680000 222163.6200000   
plu3         184.9900000    768.7820000   3466.1200000  10972.6000000   
bags_t     39743.8300000  62361.4680000  88901.7480000 149306.3600000   
bags_s     26362.8200000  46725.7540000  68884.0940000 104537.1120000   
bags_l      2647.7100000   6087.7960000  14392.2060000  34350.9860000   
bags_lx        0.0000000      0.0000000     20.2520000    557.1140000   

                      90%              max            IQR         median  \
price           1.9300000        3.2500000      0.5600000      1.3700000   
total_vol 1387045.7600000 62505646.5200000 422123.7100000 107376.7600000   
plu1       538385.1840000 22743616.1700000 110166.1300000   8645.3000000   
plu2       500784.5520000 20470572.6100000 147198.0800000  29061.0200000   
plu3        31492.4420000  2546439.1100000   6243.4200000    184.9900000   
bags_t     442141.9280000 19373134.3700000 105694.7300000  39743.8300000   
bags_s     354266.8520000 13384586.8000000  80488.2500000  26362.8200000   
bags_l      94295.3380000  5719096.6100000  21901.7800000   2647.7100000   
bags_lx      3688.9120000   551693.6500000    132.5000000      0.0000000   

                        variance   skewness     kutosis  
price                  0.1621484  0.5803027   0.3251959  
total_vol 11926975521801.3300781  9.0076875  92.1044578  
plu1       1600197376979.0056152  8.6482198  86.8091126  
plu2       1449905940429.6318359  8.9424656  91.9490220  
plu3         11548526004.6833668 10.1593956 132.5634409  
bags_t      972674070012.1464844  9.7560717 112.2721565  
bags_s      556782376190.5760498  9.5406600 107.0128851  
bags_l       59519391857.5532761  9.7964546 117.9994810  
bags_lx        313038521.1637397 13.1397507 233.6026119

## Correlation between columns

- df_stats.corr() calculates the Pearson coefficient which is used to evaluate the linear relationship between variables.
- Spearman's coefficient is used to identify monotonic relationships between variables.

Both these coefficients range between -1 to + 1. Higher positive values or negative values indicate a strong positive or negative relationship between attributes.

Looking at the below given correlation matrix we can interpret that the total_vol column is postively related with plu1, plu2, plu3, bags_t and bags_s columns i.e. as these 5 columns would increase so will the total_vol.

It also indicates that the total_vol can be predicted if we have the data for these columns using machine learning models.


In [101]:
# calculate Pearson's coefficient
df_stats.corr()

price  total_vol       plu1       plu2       plu3     bags_t  \
price      1.0000000 -0.1927524 -0.2083170 -0.1729278 -0.1794460 -0.1770879   
total_vol -0.1927524  1.0000000  0.9778632  0.9741808  0.8722023  0.9630471   
plu1      -0.2083170  0.9778632  1.0000000  0.9261100  0.8333891  0.9200566   
plu2      -0.1729278  0.9741808  0.9261100  1.0000000  0.8878550  0.9057875   
plu3      -0.1794460  0.8722023  0.8333891  0.8878550  1.0000000  0.7923143   
bags_t    -0.1770879  0.9630471  0.9200566  0.9057875  0.7923143  1.0000000   
bags_s    -0.1747298  0.9672382  0.9252799  0.9160312  0.8027330  0.9943346   
bags_l    -0.1729400  0.8806396  0.8386450  0.8100152  0.6984710  0.9430091   
bags_lx   -0.1175916  0.7471574  0.6993773  0.6888087  0.6798611  0.8042326   

              bags_s     bags_l    bags_lx  
price     -0.1747298 -0.1729400 -0.1175916  
total_vol  0.9672382  0.8806396  0.7471574  
plu1       0.9252799  0.8386450  0.6993773  
plu2       0.9160312  0.8100152  0.6888087  
plu3       0.8027330  0.6984710  0.6798611  
bags_t     0.9943346  0.9430091  0.8042326  
bags_s     1.0000000  0.9025889  0.8068446  
bags_l     0.9025889  1.0000000  0.7108584  
bags_lx    0.8068446  0.7108584  1.0000000

In [102]:
# calculate Spearman rank coefficient
df_stats.corr(method="spearman")

price  total_vol       plu1       plu2       plu3     bags_t  \
price      1.0000000 -0.6122391 -0.5961702 -0.5137317 -0.5328254 -0.5969725   
total_vol -0.6122391  1.0000000  0.9028866  0.9400249  0.8282228  0.9525495   
plu1      -0.5961702  0.9028866  1.0000000  0.7939392  0.7548383  0.8371210   
plu2      -0.5137317  0.9400249  0.7939392  1.0000000  0.8199051  0.8569463   
plu3      -0.5328254  0.8282228  0.7548383  0.8199051  1.0000000  0.7793233   
bags_t    -0.5969725  0.9525495  0.8371210  0.8569463  0.7793233  1.0000000   
bags_s    -0.5364032  0.9258737  0.8220363  0.8337638  0.7801854  0.9610185   
bags_l    -0.5111416  0.7020675  0.6385351  0.6354653  0.5718689  0.7530436   
bags_lx   -0.4272071  0.6599488  0.6155346  0.6288931  0.6528066  0.6525819   

              bags_s     bags_l    bags_lx  
price     -0.5364032 -0.5111416 -0.4272071  
total_vol  0.9258737  0.7020675  0.6599488  
plu1       0.8220363  0.6385351  0.6155346  
plu2       0.8337638  0.6354653  0.6288931  
plu3       0.7801854  0.5718689  0.6528066  
bags_t     0.9610185  0.7530436  0.6525819  
bags_s     1.0000000  0.6035817  0.6417963  
bags_l     0.6035817  1.0000000  0.5005900  
bags_lx    0.6417963  0.5005900  1.0000000

In [103]:
# plot scatter matrix for entire data set
fig = px.scatter_matrix(df_product_a)
iplot(fig)

## Resampling data

The given data includes observations for particular days. In order to summarise the weekly and monthly data we have to perform down sampling on the observations. 

For monthly down sampling the no of observations will be reduced to 12 (months) * 4 (years) = 48 obs. Similarly for the weekly data no of observation will be reduced to 169.

As the sample size is reduced we use a aggregate function to summarise the monthly and weekly data. Here we use mean().

In [104]:
# copy date_w to the summary statistics df to perform resampling on it
df_stats['date_w'] = df_product_a['date_w']

# set date_w as the index column as in order to perform resampling date_w has to be index column
df_stats.set_index('date_w', inplace = True)

# summarise monthly data using mean()
df_stats_monthly = df_stats.resample('M').mean()

df_stats_monthly.head(5)

price      total_vol           plu1           plu2  \
date_w                                                              
2016-01-31 1.3414444 810256.3793333 330598.6155926 335086.7834259   
2016-02-29 1.3429398 769951.8686111 321266.1265046 302913.7598843   
2016-03-31 1.3747222 761917.1909954 322655.1322917 288634.3171991   
2016-04-30 1.3635370 844326.3648704 367263.5024815 316374.0822037   
2016-05-31 1.3598843 861093.0622917 383092.9531481 309010.8894907   

                    plu3         bags_t         bags_s        bags_l  \
date_w                                                                 
2016-01-31 23337.2311296 121233.7491852  98640.6482037 22103.4802593   
2016-02-29 22320.9228704 123451.0593519 105398.3522222 17480.7906713   
2016-03-31 22200.0722222 128427.6692824 110795.0894213 17077.9313194   
2016-04-30 23266.8781111 137421.9020741 114985.5865741 21891.3157778   
2016-05-31 22876.8063426 146112.4133102 125007.8284259 20569.0567824   

               bags_lx  
date_w                  
2016-01-31 489.6207222  
2016-02-29 571.9164583  
2016-03-31 554.6485417  
2016-04-30 544.9997222  
2016-05-31 535.5281019

In [105]:
# summarise weekly data using mean()
df_stats_weekly = df_stats.resample('W').mean()
df_stats_weekly.head(5)

price       total_vol           plu1           plu2  \
date_w                                                               
2016-01-03 1.3012963  784021.6407407 306465.3587037 341213.3187963   
2016-01-10 1.3706481  727368.5855556 287260.7869444 303781.7577778   
2016-01-17 1.3911111  725822.0748148 294469.5079630 293167.0549074   
2016-01-24 1.3971296  708021.1210185 299121.6006481 267862.2441667   
2016-01-31 1.2470370 1106048.4745370 465675.8237037 469409.5414815   

                    plu3         bags_t         bags_s        bags_l  \
date_w                                                                 
2016-01-03 21100.1725926 115242.7906481  91759.3416667 23015.3324074   
2016-01-10 21751.5504630 114574.4903704  95860.5224074 18313.2592593   
2016-01-17 20446.7643519 117738.7475926  97674.5750926 19866.5382407   
2016-01-24 19244.2487037 121793.0275000 100715.8976852 20859.4066667   
2016-01-31 34143.4195370 136819.6898148 107192.9041667 28462.8647222   

                bags_lx  
date_w                   
2016-01-03  468.1165741  
2016-01-10  400.7087037  
2016-01-17  197.6342593  
2016-01-24  217.7231481  
2016-01-31 1163.9209259

## Monthly summarization

Below line plot shows the mean values for all the numerical attributes. 

Attributes 'price' and 'bags_lx' range in hundreds and thousands and hence appear as a straight line on the plot as the range for remaining attributes is very large. Rest all the attributes except 'total_vol' share y axis where as total_vol uses the secondary y-axis as it ranges in millions.

One of the most important insight that is obtained from the below plot is that the total_vol gradually increases in the first half of the year and then decreases by the end of the year.

Apart from that the mean of bags_t and bags_s have increased by 4 and 3 times respectively from 2016 to 2019. 
On the other hand there has been a small decrease between the mean of plu1 and plu2 during the given time span.

In [116]:
colors = plotly_colors.qualitative.Plotly

# assign y-axis for each attribute (True: use secondary y-axis)
secondary_axis = [False, True, False, False, False, False, False, False, False, False]

fig = make_subplots(specs=[[{"secondary_y": True}]])

# iterate over numeric columns to plot line graph for monthly data
for i, col in enumerate(df_stats_monthly.columns):
    fig.add_trace(go.Scatter(x = df_stats_monthly.index, y = df_stats_monthly[col], name = col, 
                    marker = dict(color = colors[i]), mode = 'lines+markers'), secondary_y = secondary_axis[i])

fig.update_layout(title="Line plots for monthly data")
iplot(fig)

## Weekly summarization

Below weekly line plot shows similar trends as compared to the monthly line plot for the total_vol attribute

Looking closely at the attribute spikes we can see that the total_vol is highly dependent on the plu2 attribute as they both follow nearly similiar upward and downward trends. In addition to that other attributes like plu1 and bags_t also contribute in determining the trend for the total_vol col

In [117]:
# assign y-axis for each attribute (True: use secondary y-axis)
secondary_axis = [False, True, False, False, False, False, False, False, False, False]

fig = make_subplots(specs=[[{"secondary_y": True}]])

# iterate over numeric columns to plot line graph for monthly data
for i, col in enumerate(df_stats_weekly.columns):
    fig.add_trace(go.Scatter(x = df_stats_weekly.index, y = df_stats_weekly[col], name = col, 
                    marker = dict(color = colors[i]), mode = 'lines+markers'), secondary_y = secondary_axis[i])

fig.update_layout(title="Line plots for weekly data")
iplot(fig)

#### Comparision of total_vol for Product type A and C

We can clearly see that the average total_vol for Product A is much higher than that of Product C


In [118]:
fig = go.Figure(layout=go.Layout({'title': "Total volume for different two types of products in different years", 
                                 'yaxis_title': "Total volume", 
                                 'xaxis_title': "Year"})

# plot bar plot for mean total_vol for both products for years ranging from 2016-2019
for i,c_type in enumerate(df_product_a['type'].unique()):
    fig.add_trace(go.Bar(x=df_product_a['year'].unique(), 
                         y=df_product_a[df_product_a['type'] == c_type].groupby('year')['total_vol'].mean(),
                         name = c_type,
                         offsetgroup = i))
    
iplot(fig)

#### Grouped Bar chart of total_vol for different states during a span of 4 years

In [156]:
fig = go.Figure(layout=go.Layout({'title': "Total volume based on locations in different years", 
                                 'yaxis_title': "Total volume", 
                                 'xaxis_title': "Year"}))

for i, loc in enumerate(df_product_a['location'].unique()):
    if loc != 'TotalUS':
        fig.add_trace(go.Bar(x=df_product_a['year'].unique(), 
                             y=df_product_a[df_product_a['location'] == loc].groupby('year')['total_vol'].sum(),
                             name=loc,
                             offsetgroup = i))
    
iplot(fig)

- The first and foremost insight indicated from the above graph is that the total_volume drops significantly in 2019 when c compared to the previous years.

- Also, the total_vol for some of the major cities/regions like California, North East, Los Angeles and South Central are almost five folds than the total_vol of the other regions and cities for all the 4 years

#### Average price values for different regions/states of USA

In [124]:
fig = go.Figure(layout=go.Layout({'title': "Average price in different regions", 
                                 'yaxis_title': "Average price", 
                                 'xaxis_title': "Location",
                                 'showlegend': False}))

fig.add_trace(go.Scatter(x = df_product_a['location'].unique(), 
                             y = df_product_a.groupby('location')['price'].mean(),
                             mode = 'lines'))
iplot(fig)

From the above line plot we can identify that cities like Hartford Springfield, New York and San Francisco have the highest mean price. On contrary, Dallas Ft Worth, Houston and South central have the lowest mean price

#### Price distribution for Product A and Product C

In [94]:
fig = go.Figure(layout=go.Layout({'title': "Price distribution for two types", 
                                 'yaxis_title': "Frequency", 
                                 'xaxis_title': "Price"}))

for i, product in enumerate(df_product_a['type'].unique()):
    fig.add_trace(go.Histogram(x=df_product_a[df_product_a['type'] == product]['price'], 
                         name = product))
    
iplot(fig)

The above histogram shows that the prices of Product C tends to be higher than that of the Product A. 

Also, the price distribution is more skewed for product C than that of Product A

#### Average prices for different location in USA for both Product type A and C

In [127]:
fig = go.Figure(layout=go.Layout({'title': "Average price in different regions", 
                                 'yaxis_title': "Average price", 
                                 'xaxis_title': "Location"}))

fig.add_trace(go.Scatter(x = df_product_a['location'].unique(), 
                         y = df_product_a[ df_product_a['type'] == 'A'].groupby('location')['price'].mean(),
                         mode = 'lines',
                         name = 'A'))
fig.add_trace(go.Scatter(x = df_product_a['location'].unique(), 
                         y = df_product_a[ df_product_a['type'] == 'C'].groupby('location')['price'].mean(),
                         mode = 'lines',
                         name = 'C'))
    
iplot(fig)

In [14]:
# store all the region names to obtain the Geo co-ordinates
addresses = df_product_a['location'].unique().tolist()

# data frame to store longitudes and latitudes from Google, Here and ArcGis APIs
co_ordinates_df = pd.DataFrame()

# list to store longitude, latitudes and Abbreviation names of the regions
long_x, lat_y, region_abbr = [], [], []

In [ ]:
google_api_key = ''

def get_geo_coordinates_from_google(address:str, connection_paras:dict):
    """
    This function returns the longitude and latitude of the location passed. Returns -,- if co-ordinates are not found
    """
    
    # append USA after the location name to indicate the country of the location
    address += ", USA"
    
    # extract the api key from the dict passed
    api_key = connection_paras['google_api_key']
    
    # create the end point by passing the address and the api key passed
    end_point = f"https://maps.googleapis.com/maps/api/geocode/json?address={address}&key={api_key}"
    
    # send a get request and store the json results
    json_location = requests.get(end_point).json()['results']
    
    # if the json result is not obtained than store the co-ordinates
    if len(json_location) > 0:
        co_ords = {'long_x': json_location[0]['geometry']['location']['lng'],
                'lat_y': json_location[0]['geometry']['location']['lat']}
    else:
        # else print the name of the location for which co-ordinates are not obtained
        print(address)
        co_ords = {'long_x': '-',
                'lat_y': '-'}
    
    # return the results
    return co_ords

for address in addresses:
    # for each address location in the addresses list send a get request to obtain the co-ordinates
    co_ords = get_geo_coordinates_from_google(address, {'google_api_key': google_api_key})
   
    # store the long and lat in the list
    long_x.append(co_ords['long_x'])
    lat_y.append(co_ords['lat_y'])
    
# add the longitude and latitude in the co-ordinates dataframe
co_ordinates_df['City'] = addresses
co_ordinates_df['GoogleLong'] = long_x
co_ordinates_df['GoogleLat'] = lat_y

In [ ]:
here_api_key = ''
long_x, lat_y = [], []

def get_geo_coordinates_from_here(address:str, connection_paras:dict):
    """
    This function returns the longitude and latitude of the location passed. Returns -,- if co-ordinates are not found
    """
    
    # append USA after the location name to indicate the country of the location
    address += ", USA"
    
    # get the api key of HERE 
    api_key = connection_paras['here_api_key']
    
    # create the end point using the address and api key
    end_point = f"https://geocoder.ls.hereapi.com/6.2/geocode.json?apiKey={api_key}&searchtext={address}"
    
    # send a get request to the HERE api to get the result
    json_location = requests.get(end_point).json()['Response']['View']
    
    # is result json is not empty than store the co-ordinates
    if len(json_location) > 0:
        co_ords = {'long_x': json_location[0]['Result'][0]['Location']['DisplayPosition']['Longitude'],
                   'lat_y': json_location[0]['Result'][0]['Location']['DisplayPosition']['Latitude']}
    else:
        # else print the location name for which co-ordinates are not obtained
        print(address)
        co_ords = {'long_x': '-',
                   'lat_y': '-'}
        
    # returns the co-ordinates
    return co_ords

for address in addresses:
    # for each address location in the addresses list send a get request to obtain the co-ordinates 
    co_ords = get_geo_coordinates_from_here(address, {'here_api_key': here_api_key})
    
    long_x.append(co_ords['long_x'])
    lat_y.append(co_ords['lat_y'])
    
# append the lat and long in the co-ordinates dataframe
co_ordinates_df['HereLong'] = long_x
co_ordinates_df['HereLat'] = lat_y

In [15]:
long_x, lat_y = [], []

# login to the ArcGis server using your username and password
gis = GIS("http://www.arcgis.com", "", "")

# send batch request to the ArcGis server to obtain long and lat for all the addresses
arc_gis_loc = batch_geocode(addresses, source_country = 'USA')

# loop over the result json obtained from the ArcGis API
for i, result in enumerate(arc_gis_loc):
    
    # extract and store the region abbreviation from the result json
    region_abbr.append(result['attributes']['RegionAbbr'])
    
    # is result json is not empty for that location than store the lat and long
    if result['address'] != '':
        long_x.append(result['location']['x'])
        lat_y.append(result['location']['y'])
    else:
        # else store - and display the name of the location for which co-ordinates are not obtained
        long_x.append('-')
        lat_y.append('-')
        print(addresses[i] + " --")
        
# store the details obtained from the ArcGis API in a dataframe
co_ordinates_df['ArcLong'] = long_x
co_ordinates_df['ArcLat'] = lat_y
co_ordinates_df['RegionAbbr'] = region_abbr

MiamiFtLauderdale
WestTexNewMexico


- From the above three APIs used we can see that the HERE api is least reliable as the no of co-ordinates are higher than that of Google and ArcGis combined.
- Apart from that the latency of ArcGis API is less as compared to that of Google API as I use batch_geocode to send a single request to obtain the co-ordinates for all the location.
- However the latitude and longitude provided by the Google API are more accurate as ArcGis contain certail co-ordinates like lie beyond the borders of USA


In [ ]:
co_ordinates_df.head(5)

## Folium Map Visualisation

In [18]:
# store following information in the co-ordinates dataframe to visualize required data on folium map

# store the mean of bags_t grouped by location
co_ordinates_df['mean_bags_t'] = df_product_a.groupby('location')['bags_t'].mean().tolist()
# store the total count of bags_t grouped by location
co_ordinates_df['total_bags_t'] = round(df_product_a.groupby('location')['bags_t'].sum(), 4).tolist()
# store the total count of bags_t for Product A grouped by location
co_ordinates_df['total_bags_t_A'] = round(df_product_a.groupby(['location', 'type'])['bags_t'].sum(), 2).tolist()[::2]
# store the total count of bags_t for Product C grouped by location
co_ordinates_df['total_bags_t_C'] = round(df_product_a.groupby(['location', 'type'])['bags_t'].sum(), 2).tolist()[1::2]
# store the mean of price for Product A grouped by location
co_ordinates_df['mean_price_A'] = round(df_product_a.groupby(['location', 'type'])['price'].mean(), 2).tolist()[::2]

# calculate summary statistics of data frame grouped by location and store it in the co-ordinates df
mean_df = df_product_a.groupby('location').mean().reset_index()
co_ordinates_df[mean_df.columns] = round(mean_df, 2)

# sort the co-ordinates df in ascending order of mean values of bags_t
co_ordinates_df.sort_values(by = ['mean_bags_t'], inplace = True)
# after sorting create a column to store colors in terms of 5 bins to visualize on folium map
co_ordinates_df['colors'] = ['#edf8b1'] * 11 + ['#7fcdbb']*11 + ['#2c7fb8']*11 + ['#feb24c']*11 + ['#f03b20']*10

colors = ['#edf8b1', '#7fcdbb', '#2c7fb8', '#feb24c', '#f03b20']

In [19]:
# create an object of folium map zoomed in to USA with the CartoDB map tile
map = folium.Map(location=[38, -102], zoom_start=4.3, tiles='CartoDB dark_matter')

# loop over co-ordinates df to plot the longitudes and latitudes for each location
for row in co_ordinates_df.iterrows():
    
    # plot the data using Google co-ordinates if co-ordinates are obtained for that location
    if row[1].GoogleLong != '-':
        
        # store  total bags_t count, bags_t_A count and bags_t_C count to be displayed on tooltip
        tooltip = row[1].location + "<br>Total Bag_t: " + str(row[1].total_bags_t) + "<br>A: " + str(row[1].total_bags_t_A) + "<br>C: " + str(row[1].total_bags_t_C)
        
        # store numeric fields details to be diplayed on the popup
        popup = folium.Popup("Price: " + str(row[1].price) + "<br>Total volume: " + str(row[1].total_vol) + "<br>Plu1: " + str(row[1].plu1) + "<br>Plu2: " + str(row[1].plu2) + "<br>Plu3: " + str(row[1].plu3) + "<br>Bags_t: " + str(row[1].bags_t) + "<br>Bag_l: " + str(row[1].bags_l) + "<br>Bags_s: " + str(row[1].bags_s) + "<br>Bags_lx: " + str(row[1].bags_lx), max_width=170)
        
        # create circle markers for the folium map on specific lat and long
        folium.CircleMarker(location=[row[1].GoogleLat, row[1].GoogleLong],
                            radius= row[1].mean_price_A*12, # assign radius based on the mean value of price for Product A
                            popup=popup,
                            stroke = False,
                            color='#FFFFFF',
                            opacity= 1,
                            fill_opacity=1,
                            fill=True,
                            fill_color=row[1].colors, 
                            tooltip=tooltip).add_to(map)

state_geo = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data/us-states.json'

# create a Choropleth to display the state border using the us-states.json Geo json file
folium.Choropleth(
    geo_data=state_geo, 
    name='choropleth', 
    fill_color=False, 
    fill_opacity = 0,
    data=co_ordinates_df, 
    columns=['RegionAbbr', 'mean_bags_t'], 
    key_on='feature.id',
    line_color= 'white', 
    line_opacity=0.4, 
    line_weight = 0.6, 
    legend_name='Mean of bags_t'
).add_to(map)

folium.LayerControl().add_to(map)
map